In [49]:
import pandas as pd
import urllib
import matplotlib.pyplot as plt

In [ ]:
STATE_POP_DATA='SCPRC-EST2019-18+POP-RES.csv'
STATE_ABREV='state_abrev.json'
COVID_DATA_URL='https://covidtracking.com/api/v1/states/daily.json'
COVID_OUTPUT_FILE_NAME='covid_data.json'
GET_FIELDS_STATE=['NAME', 'POPESTIMATE2019']
GET_FIELDS_COVID=['date','state','positive','negative','death', 'positiveIncrease','negativeIncrease', 'totalTestResults']
ALL_FIELDS=['date','state','POPESTIMATE2019','positive','negative','death', 'positiveIncrease','negativeIncrease','totalTestResults']
OUTPUT_LIST=['mortality %', 'death %']
STATES=['all']
if 'all' in STATES:
    STATES = ["AL", "AK", "AZ", "AR", "CA", "CO", "CT", "DC", "DE", "FL", "GA",
          "HI", "ID", "IL", "IN", "IA", "KS", "KY", "LA", "ME", "MD",
          "MA", "MI", "MN", "MS", "MO", "MT", "NE", "NV", "NH", "NJ",
          "NM", "NY", "NC", "ND", "OH", "OK", "OR", "PA", "RI", "SC",
          "SD", "TN", "TX", "UT", "VT", "VA", "WA", "WV", "WI", "WY"]
DEBUG=False
LOAD_NEW_DATA=False
PRINT_RAW_DATA=False


In [48]:
def load_data_and_save(url, output_file_name):
    if LOAD_NEW_DATA == True:
        print(f'Loading data from {url} and saving to {output_file_name}...')
        uh = urllib.request.urlopen(url)
        data = uh.read().decode()
        file = open(output_file_name, 'w')
        file.write(data)
        file.close()
        debug(f'Loaded data: \n {data}')
        debug(f'Data saved to \n {output_file_name}')
    else:
        print(f'New data not loaded, reading from {output_file_name}. Set LOAD_NEW_DATA=True to load data')

def debug(message):
    if DEBUG == True:
        print(message)

def load_states(data):
    print('Loading states...')
    state_data_lst=[]
    for state in STATES:
        print(state)
        state_data_lst.append(state_data(data, state))
    debug(f'loaded states: \n {state_data_lst}')
    return state_data_lst

def state_data(data, state):
    state_data= data.query(f'state == "{state}"')
    debug(f'Loaded state data list ({state}): \n {state_data}')
    return state_data

In [39]:
def parse_to_pd(data_file_name):
    print(f'Reading data from {data_file_name}...')
    data=pd.read_json(data_file_name)
    debug(data.columns)
    data['date']=pd.to_datetime(data['date'], format='%Y%m%d')
    state_pop=pd.read_csv(STATE_POP_DATA)
    state_abrev=pd.read_json(STATE_ABREV)
    states=pd.merge(state_abrev, state_pop, left_on="name", right_on="NAME")
    data=pd.merge(states, data.get(GET_FIELDS_COVID), left_on='abbreviation', right_on='state')
    data=data.get(ALL_FIELDS)
    debug(f'Parsed data: \n {data}')
    debug(data.columns)
    return data



In [40]:
def analyse(data):
    print(f'Analysing Data...')
    for state in data:       
        state['positive %'] = (state['positive'] / state['POPESTIMATE2019']) * 100
        state['negative %']  = (state['negative'] / state['POPESTIMATE2019']) * 100
        state['death %'] = (state['death'] / state['POPESTIMATE2019']) * 100
        state['mortality %'] = (state['death'] / state['positive']) * 100
        state['tested %'] = (state['totalTestResults'] / state['POPESTIMATE2019']) * 100
        state['positive/negative %'] = (state['positive'] / state['negative']) * 100
        state['new test positive %'] = (state['positiveIncrease'] / state['negativeIncrease']) * 100
        debug(f'Analysed {state} data: \n {data}')
    return data

In [41]:
def graph(data, states):

    return data


In [42]:
def output(data):
    if PRINT_RAW_DATA: 
        print(data)
    if DEBUG: 
        print(type(data))
        for i in data:
            print(i.size, i.shape, i.dtypes, i.columns, i.index)

    


In [47]:

def run():

    load_data_and_save(COVID_DATA_URL, COVID_OUTPUT_FILE_NAME)
    data = parse_to_pd(COVID_OUTPUT_FILE_NAME)
    data = load_states(data)
    data = analyse(data)
    output(data)
    graph(data, STATES)

run()


Loading data from https://covidtracking.com/api/v1/states/daily.json and saving to covid_data.json...


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Index(['date', 'state', 'positive', 'negative', 'pending',
       'hospitalizedCurrently', 'hospitalizedCumulative', 'inIcuCurrently',
       'inIcuCumulative', 'onVentilatorCurrently', 'onVentilatorCumulative',
       'recovered', 'dataQualityGrade', 'lastUpdateEt', 'dateModified',
       'checkTimeEt', 'death', 'hospitalized', 'dateChecked',
       'totalTestsViral', 'positiveTestsViral', 'negativeTestsViral',
       'positiveCasesViral', 'deathConfirmed', 'deathProbable', 'fips',
       'positiveIncrease', 'negativeIncrease', 'total', 'totalTestResults',
       'totalTestResultsIncrease', 'posNeg', 'deathIncrease',
       'hospitalizedIncrease', 'hash', 'commercialScore',
       'negativeRegularScore', 'negativeScore', 'positiveScore', 'score',
       'grade'],
      dtype='object')
Parsed data: 
            date state  POPESTIMATE2019  positive  negative   death  \
0    2020-07-11    AL          4903185   51947.0  450073.0  1114.0   
1    2020-07-10    AL          4903185   50508.0

Loaded state data list (IL): 
            date state  POPESTIMATE2019  positive   negative   death  \
1541 2020-07-11    IL         12671821  154094.0  1791126.0  7369.0   
1542 2020-07-10    IL         12671821  152899.0  1759976.0  7345.0   
1543 2020-07-09    IL         12671821  151572.0  1728306.0  7329.0   
1544 2020-07-08    IL         12671821  150554.0  1693144.0  7309.0   
1545 2020-07-07    IL         12671821  149574.0  1661382.0  7273.0   
...         ...   ...              ...       ...        ...     ...   
1666 2020-03-08    IL         12671821       6.0      191.0     NaN   
1667 2020-03-07    IL         12671821       6.0      191.0     NaN   
1668 2020-03-06    IL         12671821       5.0      180.0     NaN   
1669 2020-03-05    IL         12671821       5.0      165.0     NaN   
1670 2020-03-04    IL         12671821       4.0      124.0     NaN   

      positiveIncrease  negativeIncrease  totalTestResults  
1541              1195             31150           1945

Loaded state data list (NH): 
            date state  POPESTIMATE2019  positive  negative  death  \
3588 2020-07-11    NH          1359711    5991.0  126311.0  390.0   
3589 2020-07-10    NH          1359711    5973.0  125078.0  387.0   
3590 2020-07-09    NH          1359711    5952.0  123676.0  386.0   
3591 2020-07-08    NH          1359711    5932.0  122579.0  384.0   
3592 2020-07-07    NH          1359711    5914.0  121966.0  382.0   
...         ...   ...              ...       ...       ...    ...   
3713 2020-03-08    NH          1359711       4.0      38.0    NaN   
3714 2020-03-07    NH          1359711       2.0      20.0    NaN   
3715 2020-03-06    NH          1359711       2.0      20.0    NaN   
3716 2020-03-05    NH          1359711       2.0      16.0    NaN   
3717 2020-03-04    NH          1359711       2.0      10.0    NaN   

      positiveIncrease  negativeIncrease  totalTestResults  
3588                18              1233            132302  
3589              

...

Analysed            date state  POPESTIMATE2019  positive  negative   death  \
5909 2020-07-11    WA          7614893   39218.0  629248.0  1424.0   
5910 2020-07-10    WA          7614893   38581.0  621749.0  1409.0   
5911 2020-07-09    WA          7614893   37941.0  607131.0  1394.0   
5912 2020-07-08    WA          7614893   37420.0  598104.0  1384.0   
5913 2020-07-07    WA          7614893   36985.0  592271.0  1370.0   
...         ...   ...              ...       ...       ...     ...   
6076 2020-01-26    WA          7614893       2.0       0.0     NaN   
6077 2020-01-25    WA          7614893       2.0       0.0     NaN   
6078 2020-01-24    WA          7614893       2.0       0.0     NaN   
6079 2020-01-23    WA          7614893       2.0       0.0     NaN   
6080 2020-01-22    WA          7614893       2.0       0.0     NaN   

      positiveIncrease  negativeIncrease  totalTestResults  positive %  \
5909               637              7499            668466    0.515017   
59

Analysed            date state  POPESTIMATE2019  positive  negative  death  \
6081 2020-07-11    WV          1792147    4074.0  199749.0   95.0   
6082 2020-07-10    WV          1792147    3983.0  197220.0   95.0   
6083 2020-07-09    WV          1792147    3826.0  193363.0   95.0   
6084 2020-07-08    WV          1792147    3707.0  190208.0   95.0   
6085 2020-07-07    WV          1792147    3461.0  186386.0   95.0   
...         ...   ...              ...       ...       ...    ...   
6204 2020-03-10    WV          1792147       0.0       2.0    NaN   
6205 2020-03-09    WV          1792147       0.0       2.0    NaN   
6206 2020-03-08    WV          1792147       0.0       2.0    NaN   
6207 2020-03-07    WV          1792147       0.0       2.0    NaN   
6208 2020-03-06    WV          1792147       0.0       1.0    NaN   

      positiveIncrease  negativeIncrease  totalTestResults  positive %  \
6081                91              2529            203823    0.227325   
6082          

Analysed            date state  POPESTIMATE2019  positive  negative  death  \
6209 2020-07-11    WI          5822434   39080.0  646504.0  828.0   
6210 2020-07-10    WI          5822434   38099.0  635411.0  821.0   
6211 2020-07-09    WI          5822434   37210.0  623554.0  816.0   
6212 2020-07-08    WI          5822434   36410.0  611150.0  814.0   
6213 2020-07-07    WI          5822434   35765.0  601012.0  812.0   
...         ...   ...              ...       ...       ...    ...   
6334 2020-03-08    WI          5822434       1.0      31.0    NaN   
6335 2020-03-07    WI          5822434       1.0      31.0    NaN   
6336 2020-03-06    WI          5822434       1.0      31.0    NaN   
6337 2020-03-05    WI          5822434       1.0      19.0    NaN   
6338 2020-03-04    WI          5822434       1.0      19.0    NaN   

      positiveIncrease  negativeIncrease  totalTestResults  positive %  \
6209               981             11093            685584    0.671197   
6210          

Analysed            date state  POPESTIMATE2019  positive  negative  death  \
6339 2020-07-11    WY           578759    1839.0   38077.0   21.0   
6340 2020-07-10    WY           578759    1790.0   38077.0   21.0   
6341 2020-07-09    WY           578759    1774.0   37271.0   21.0   
6342 2020-07-08    WY           578759    1740.0   36078.0   21.0   
6343 2020-07-07    WY           578759    1711.0   36078.0   20.0   
...         ...   ...              ...       ...       ...    ...   
6461 2020-03-11    WY           578759       0.0       NaN    NaN   
6462 2020-03-10    WY           578759       0.0       0.0    NaN   
6463 2020-03-09    WY           578759       0.0       NaN    NaN   
6464 2020-03-08    WY           578759       0.0       NaN    NaN   
6465 2020-03-07    WY           578759       0.0       NaN    NaN   

      positiveIncrease  negativeIncrease  totalTestResults  positive %  \
6339                49                 0             39916    0.317749   
6340          

[          date state  POPESTIMATE2019  positive  negative   death  \
0   2020-07-11    AL          4903185   51947.0  450073.0  1114.0   
1   2020-07-10    AL          4903185   50508.0  441708.0  1104.0   
2   2020-07-09    AL          4903185   49174.0  421330.0  1068.0   
3   2020-07-08    AL          4903185   46962.0  421330.0  1058.0   
4   2020-07-07    AL          4903185   45785.0  415579.0  1033.0   
..         ...   ...              ...       ...       ...     ...   
122 2020-03-11    AL          4903185       0.0      10.0     NaN   
123 2020-03-10    AL          4903185       0.0       0.0     NaN   
124 2020-03-09    AL          4903185       0.0       NaN     NaN   
125 2020-03-08    AL          4903185       0.0       NaN     NaN   
126 2020-03-07    AL          4903185       0.0       NaN     NaN   

     positiveIncrease  negativeIncrease  totalTestResults  positive %  \
0                1439              8365            502020    1.059454   
1                1334   